# Práctica NLP - Word2vec 
## Marta Castañeda Albillos

En esta práctica se va a hacer uso de los modelos de tipo Word2vec. Word2vec es un grupo de modelos relacionados que se utilizan para producir incrustaciones de palabras. Estos modelos son redes neuronales superficiales de dos capas que están entrenadas para reconstruir contextos lingüísticos de palabras. Word2vec toma como entrada un gran corpus de texto y produce un espacio vectorial, típicamente de varios cientos de dimensiones, a cada palabra única en el corpus se le asigna un vector correspondiente en el espacio. Los vectores de palabras se colocan en el espacio vectorial de tal manera que las palabras que comparten contextos comunes en el corpus se ubican cerca unas de otras en el espacio. (https://en.wikipedia.org/wiki/Word2vec)

Para realizar un análisis en los que los datos de entrada son texto es importante hacer una transformación y limpieza previa de tal manera que se represente mediante vectores de palabras.

Se va a hacer uso de un corpus de Miguel de Cervantes (gutenberg.org/cache/epub/2000/pg2000.txt) que corresponde al Proyecto Gutenberg. Con este, se va a crear y entrenar un modelo word2vec con el vocabulario generado mediante las palabras que contiene dicho corpus. 

Inicialmente, se ha realizado una limpieza del mismo: eliminando símbolos (puntos, comas, etc.), convirtiendo todo a minúsculas y tokenizandolo. Después se ha filtrado eliminando los tokens que se consideran stopwords y se han estemizado. Tras ello, se ha creado y entrenado el modelo word2vec, el cual se ha interrogado a través de un CSV que contiene canciones de RAP.

In [6]:
import pandas as pd
import numpy as np
import gensim.models.word2vec as w2v
import multiprocessing
import os
import re
import pprint
import sklearn.manifold
import matplotlib.pyplot as plt

from nltk.stem.porter import PorterStemmer
from nltk.corpus import stopwords
from nltk.tokenize import RegexpTokenizer
from gensim import corpora, models
import wikipedia
import gensim

In [250]:
songs_test = pd.read_csv("data/hhgroups_merge_28_05.csv/hhgroups_merge_28_05.csv", header=0)
songs = pd.read_table("data/cervantes.txt", header=0)
#songs = pd.read_table("data/datos_spanish.txt", error_bad_lines=False)
#songs.head()
#songs = songs[songs.artist != 'Lata Mangeshkar']
songs.head()

Corpus
0  The Project Gutenberg EBook of Don Quijote, by...
1  This eBook is for the use of anyone anywhere a...
2  almost no restrictions whatsoever.  You may co...
3  re-use it under the terms of the Project Guten...
4     with this eBook or online at www.gutenberg.net

To train the word2vec model, we first need to build its vocabulary. To do that, I iterated over each song and added it to an array that can later be fed to the model.

In [252]:
songs_test.head()

id           artista                                            cancion  \
0   0             Denom             Machete (con Jarfaiter y Gente jodida)   
1   1             Denom                           Vacío (con Ivo Incuerdo)   
2   2             Denom  El orgullo es fiel (con Juancho Marqués y Elio...   
3   3             Denom                    Mueve mueve (con Fernandocosta)   
4   4  Jaro Desperdizio                                           Insomnia   

                           album  \
0                       Medicina   
1                       Medicina   
2                       Medicina   
3                       Medicina   
4  Sin álbum, es un vídeo suelto   

                                               letra  anyo  visitas  
0  Para su nuevo disco "Medicina", Denom ha vuelt...  2019      126  
1  [Denom]\nYo que quería, yo que pedía vida,\nSe...  2019      361  
2  "El orgullo es fiel" es uno de los cortes incl...  2019      262  
3  [Estribillo: Denom] (x2)\nMueve, mueve, mueve,...  2019      578  
4  [Estribillo]\nY en esta noche, ¿Quién me arrop...  2019      219

### 1. Limpieza de los datos:

In [253]:
text_corpus = []
test_data = []
for song in songs['Corpus'][13:]:
    #words = song.lower().split()
    words = RegexpTokenizer(r'\w+').tokenize(song.lower()) # guarda todo menos los símbolos tipo puntos, comas,...
    words = [token for token in words if token not in stopwords.words('spanish')] # guarda los tokens que no son stopword
    words = [PorterStemmer().stem(token) for token in words]
    text_corpus.append(words)
    
for song in songs_test['letra']:
    words = RegexpTokenizer(r'\w+').tokenize(song.lower())
    words = [token for token in words if token not in stopwords.words('spanish')] # guarda los tokens que no son stopword
    words = [PorterStemmer().stem(token) for token in words]
    test_data.append(words)

### 2. Creación del modelo Word2Vec:

In [319]:
# Dimensionality of the resulting word vectors.
#more dimensions, more computationally expensive to train
#but also more accurate
#more dimensions = more generalized
num_features = 50
# Minimum word count threshold.
min_word_count = 1

# Number of threads to run in parallel.
#more workers, faster we train
num_workers = multiprocessing.cpu_count()

# Context window length.
context_size = 7


downsampling = 1e-1

# Seed for the RNG, to make the results reproducible.
#random number generator
#deterministic, good for debugging
seed = 1

songs2vec = w2v.Word2Vec( # FUNCION PARA CREAR EL MODELO
    sg=1,
    seed=seed,
    workers=num_workers,
    size=num_features,
    min_count=min_word_count,
    window=context_size,
    sample=downsampling
)

### 3. Entrenamiento del modelo con el vocabulario del corpus:

In [320]:
songs2vec.build_vocab(text_corpus) # ENTRENO EL MODELO
print (len(text_corpus))

31916


In [165]:
#songs2vec = w2v.Word2Vec.load(os.path.join("trained", "songs2vectors.w2v"))

### 4. Exploración del modelo:

En este apartado se ha querido observar la diferencia de los words embeddings generados con el modelo preentrenado visto en prácticas anteriores. Con los siguientes resultados obtenidos se observa una gran diferencia con los del modelo preentrenado ya que las de este son mucho peores, seguramente por la calidad, cantidad y procesado que se les ha realizado a los datos de entrada en el modelo preentrenado. Dichos resultados reflejan un vocabulario poco exquisito en los que la semántica deducida deja mucho que desear.

In [330]:
songs2vec.wv.most_similar("casa")

[('reprehenda', 0.5234036445617676),
 ('vanidades', 0.5213463306427002),
 ('discurrir', 0.5167645215988159),
 ('cocía', 0.4875445067882538),
 ('fuele', 0.4848800599575043),
 ('ciñen', 0.4754151403903961),
 ('turbada', 0.47122034430503845),
 ('encarece', 0.4674760103225708),
 ('largarse', 0.46683254837989807),
 ('recogiendo', 0.4635343849658966)]

In [331]:
songs2vec.wv.most_similar("cantar")

[('duraba', 0.5427943468093872),
 ('levantados', 0.5258704423904419),
 ('creéis', 0.4787560999393463),
 ('oliscan', 0.4783444106578827),
 ('aventurando', 0.4762764573097229),
 ('resfriarme', 0.47580769658088684),
 ('trato', 0.4743206202983856),
 ('excetado', 0.47377535700798035),
 ('ahuyentado', 0.4705537259578705),
 ('fecundas', 0.46670231223106384)]

In [332]:
songs2vec.wv.doesnt_match("felicidad amor amistad odio".split())

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\gensim\models\keyedvectors.py:877: FutureWarning:

arrays to stack must be passed as a "sequence" type such as list or tuple. Support for non-sequence iterables such as generators is deprecated as of NumPy 1.16 and will raise an error in the future.



'felicidad'

In [333]:
songs2vec.most_similar(positive=['cuadra', 'mesa'], negative=['casa'])

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:1: DeprecationWarning:

Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).



[('háselo', 0.4875139594078064),
 ('mirábale', 0.4860353469848633),
 ('vehemente', 0.48222336173057556),
 ('holgó', 0.48025447130203247),
 ('levantando', 0.4679744839668274),
 ('estudios', 0.46196112036705017),
 ('vencieron', 0.4600086808204651),
 ('estirado', 0.45441868901252747),
 ('llegasen', 0.4511045515537262),
 ('acomodaría', 0.44235295057296753)]

In [334]:
def nearest_similarity_cosmul(start1, end1, end2):
    similarities = songs2vec.wv.most_similar_cosmul(
        positive=[end2, start1],
        negative=[end1]
    )
    start2 = similarities[0][0]
    print("{0} es a {1}, lo que {2} es a {3}".format(start1, end1, start2, end2))

In [365]:
nearest_similarity_cosmul("madrid", "españa", "italia")

madrid es a españa, lo que joyas es a italia


### 5. Se interroga al modelo:

Como se ha dicho anteriormente, se va a introducir unas canciones de rap para ver cómo lo analiza mediante el modelo entrenado previamente.

In [321]:
#print(songs2vec['un-right'])
def songVector(row):
    #print(row)
    vector_sum = 0
    normalised_vector_sum=0
    #words = row.lower().split()
    words = RegexpTokenizer(r'\w+').tokenize(row.lower()) # guarda todo menos los símbolos tipo puntos, comas,...
    #print(tokens)
    words = [token for token in words if token not in stopwords.words('spanish')] # guarda los tokens que no son stopword
    words = [PorterStemmer().stem(token) for token in words]
    #

    for word in words:
        try:
            vector_sum = vector_sum + songs2vec[word]
        except:
            continue
    
    if isinstance(vector_sum, int):
        print(vector_sum)
    else:
        vector_sum = vector_sum.reshape(1,-1)
        normalised_vector_sum = sklearn.preprocessing.normalize(vector_sum)
    
    return normalised_vector_sum


In [322]:
import time
start_time = time.time()

#songs['song_vector'] = songs['Corpus'][13:].apply(songVector)
songs_test['song_vector'] = songs_test['letra'].apply(songVector)

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.

...

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).

C:\Users\usuario\Anaconda3\envs\images\lib\site-packages\ipykernel_launcher.py:15: DeprecationWarning:

Call to deprecated `__getitem__` (Method will be removed in 4.0.

In [323]:
songs_test.head()

id           artista                                            cancion  \
0   0             Denom             Machete (con Jarfaiter y Gente jodida)   
1   1             Denom                           Vacío (con Ivo Incuerdo)   
2   2             Denom  El orgullo es fiel (con Juancho Marqués y Elio...   
3   3             Denom                    Mueve mueve (con Fernandocosta)   
4   4  Jaro Desperdizio                                           Insomnia   

                           album  \
0                       Medicina   
1                       Medicina   
2                       Medicina   
3                       Medicina   
4  Sin álbum, es un vídeo suelto   

                                               letra  anyo  visitas  \
0  Para su nuevo disco "Medicina", Denom ha vuelt...  2019      126   
1  [Denom]\nYo que quería, yo que pedía vida,\nSe...  2019      361   
2  "El orgullo es fiel" es uno de los cortes incl...  2019      262   
3  [Estribillo: Denom] (x2)\nMueve, mueve, mueve,...  2019      578   
4  [Estribillo]\nY en esta noche, ¿Quién me arrop...  2019      219   

                                         song_vector  
0  [[0.0030148665, 0.033869054, 0.0069745868, 0.0...  
1  [[0.25249872, 0.12017827, -0.16525172, 0.14641...  
2  [[-0.1424899, -0.050278228, -0.13866329, 0.020...  
3  [[0.1515726, -0.21834828, 0.15814933, -0.02449...  
4  [[-0.081882074, 0.10578807, 0.099915676, 0.094...

#### TSNE

Al utilizar la técnica de TSNE se han modificado los parámetros de entrada para observar cómo variaban los resultados. 

De dichos parámetros se ha deducido que es mejor poner un número de iteraciones alto, en este caso de 1000. En cuanto a la verbosidad se ha reducido su valor ya que en las canciones de rap no se suele hablar con una gran variedad de palabras y en algunas ocasiones suele ser incluso algo repetitivo. Y, por último, la perplejidad (perplexity) se ha reducido a 5 ya que el conjunto de datos no es muy grande.

In [338]:
song_vectors = []
from sklearn.model_selection import train_test_split

train, test = train_test_split(songs_test, test_size = 0.9)


for song_vector in train['song_vector']:
    song_vectors.append(song_vector)

train.head(10)

id               artista                               cancion  \
6343  43                Kase.O                      Repartiendo arte   
8455  10  Chukky y Surce Beats                           MC seductor   
871   46                 Aripa    El mundo de lo terriblemente obvio   
1919  49               3coma14     Dejandome la piel [Base Internet]   
1966  41            MC Argueta               Bella (con Kanelo cent)   
447    7          Luky Lacatox                                All in   
3894  44          La excepción                     No se puede primo   
926   46       Piezas y Jayder  Un desencanto encantador (con Neusi)   
4302  12           Arma Blanca                             85 b.p.m.   
9061  11            Ner y STBN             Paranoias [Base Internet]   

                             album  \
6343                    El círculo   
8455               ¡Es una trampa!   
871          No apto para personas   
1919                    La mixtape   
1966  Sin álbum, es un tema suelto   
447                  Amor al juego   
3894                     Sin álbum   
926                    Mal ejemplo   
4302                   R-Evolución   
9061                     Paranoias   

                                                  letra  anyo  visitas  \
6343  [Estribillo](x2)\nRepartiendo arte, porque esa...  2016    11467   
8455  Nena Yo soy un tipo simple que hace siempre el...  2013      957   
871   No quiero que penséis que es solo una... Un pr...  2010     1458   
1919  Ye ye you you ye ye dejadome la piel en el pap...  2009     2246   
1966  Bella más radiante que el sol y que la luna,\n...  2016      208   
447   Si, Esto es amor al juego tío.\nLuky Lacatox, ...  2011     1005   
3894  Arza! y al compás te rompen\nArza! y al compás...     0      874   
926   [Estribillo]\n¿De qué sirve tener\nsi cuanto m...  2011     7735   
4302  [Madnass]\n\n\nEs fácil caer bajo mínimos\ntra...  2004     2654   
9061  Yeah... Selecta Incorporated... Ouhhh...\n\n\n...  2011      467   

                                            song_vector  
6343  [[0.32701766, 0.07369194, -0.17806709, -0.2848...  
8455  [[0.21367814, -0.17264284, 0.14315751, 0.04552...  
871   [[0.033576064, 0.11381981, 0.03323982, 0.10893...  
1919  [[0.15828276, -0.19332649, 0.03358131, -0.0077...  
1966  [[0.13633102, 0.021079788, -0.220977, -0.17637...  
447   [[0.107961014, -0.06537044, -0.09923444, -0.07...  
3894  [[0.02397894, -0.03587367, -0.078332566, -0.10...  
926   [[0.057814997, 0.019007152, -0.16801013, 0.106...  
4302  [[0.006165414, -0.1543147, -0.18430911, -0.069...  
9061  [[0.009563836, 0.05495432, 0.13821074, 0.00872...

In [340]:
X = np.array(song_vectors).reshape(len(song_vectors), 50)

#### 2-Dimensiones

In [360]:
start_time = time.time()
tsne = sklearn.manifold.TSNE(n_components=2, n_iter=1000, random_state=0, verbose=1, perplexity=5)

all_word_vectors_matrix_2d = tsne.fit_transform(X)

print("--- %s seconds ---" % (time.time() - start_time))

[t-SNE] Computing 16 nearest neighbors...
[t-SNE] Indexed 932 samples in 0.008s...
[t-SNE] Computed neighbors for 932 samples in 0.076s...
[t-SNE] Computed conditional probabilities for sample 932 / 932
[t-SNE] Mean sigma: 0.200394
[t-SNE] KL divergence after 250 iterations with early exaggeration: 97.807266
[t-SNE] KL divergence after 1000 iterations: 2.346288
--- 5.082407236099243 seconds ---


In [361]:
df=pd.DataFrame(all_word_vectors_matrix_2d,columns=['X','Y'])

df.head(10)

train.head()

df.reset_index(drop=True, inplace=True)
train.reset_index(drop=True, inplace=True)

In [362]:
two_dimensional_songs = pd.concat([train, df], axis=1)

two_dimensional_songs.head()

id               artista                             cancion  \
0  43                Kase.O                    Repartiendo arte   
1  10  Chukky y Surce Beats                         MC seductor   
2  46                 Aripa  El mundo de lo terriblemente obvio   
3  49               3coma14   Dejandome la piel [Base Internet]   
4  41            MC Argueta             Bella (con Kanelo cent)   

                          album  \
0                    El círculo   
1               ¡Es una trampa!   
2         No apto para personas   
3                    La mixtape   
4  Sin álbum, es un tema suelto   

                                               letra  anyo  visitas  \
0  [Estribillo](x2)\nRepartiendo arte, porque esa...  2016    11467   
1  Nena Yo soy un tipo simple que hace siempre el...  2013      957   
2  No quiero que penséis que es solo una... Un pr...  2010     1458   
3  Ye ye you you ye ye dejadome la piel en el pap...  2009     2246   
4  Bella más radiante que el sol y que la luna,\n...  2016      208   

                                         song_vector          X          Y  
0  [[0.32701766, 0.07369194, -0.17806709, -0.2848...  38.216145 -30.301214  
1  [[0.21367814, -0.17264284, 0.14315751, 0.04552... -16.977470  23.597178  
2  [[0.033576064, 0.11381981, 0.03323982, 0.10893...  -3.012886  16.338713  
3  [[0.15828276, -0.19332649, 0.03358131, -0.0077...  38.513187  47.551754  
4  [[0.13633102, 0.021079788, -0.220977, -0.17637... -14.500630 -53.303619

#### 3-Dimensiones

In [344]:
start_time = time.time()
tsne_3 = sklearn.manifold.TSNE(n_components=3, n_iter=1000, random_state=0, verbose=1, perplexity=5)

all_word_vectors_matrix_3d = tsne_3.fit_transform(X)

print("--- %s seconds ---" % (time.time() - start_time))

[t-SNE] Computing 16 nearest neighbors...
[t-SNE] Indexed 932 samples in 0.009s...
[t-SNE] Computed neighbors for 932 samples in 0.117s...
[t-SNE] Computed conditional probabilities for sample 932 / 932
[t-SNE] Mean sigma: 0.200394
[t-SNE] KL divergence after 250 iterations with early exaggeration: 125.618652
[t-SNE] KL divergence after 1000 iterations: 3.081339
--- 17.31509518623352 seconds ---


In [345]:
df=pd.DataFrame(all_word_vectors_matrix_3d,columns=['X','Y','Z'])

df.head(10)

train.head()

df.reset_index(drop=True, inplace=True)
train.reset_index(drop=True, inplace=True)

Joining two dataframes to obtain each song's corresponding X,Y co-ordinate.

In [346]:
three_dimensional_songs = pd.concat([train, df], axis=1)

three_dimensional_songs.head()

id               artista                             cancion  \
0  43                Kase.O                    Repartiendo arte   
1  10  Chukky y Surce Beats                         MC seductor   
2  46                 Aripa  El mundo de lo terriblemente obvio   
3  49               3coma14   Dejandome la piel [Base Internet]   
4  41            MC Argueta             Bella (con Kanelo cent)   

                          album  \
0                    El círculo   
1               ¡Es una trampa!   
2         No apto para personas   
3                    La mixtape   
4  Sin álbum, es un tema suelto   

                                               letra  anyo  visitas  \
0  [Estribillo](x2)\nRepartiendo arte, porque esa...  2016    11467   
1  Nena Yo soy un tipo simple que hace siempre el...  2013      957   
2  No quiero que penséis que es solo una... Un pr...  2010     1458   
3  Ye ye you you ye ye dejadome la piel en el pap...  2009     2246   
4  Bella más radiante que el sol y que la luna,\n...  2016      208   

                                         song_vector          X          Y  \
0  [[0.32701766, 0.07369194, -0.17806709, -0.2848... -16.792974 -16.543364   
1  [[0.21367814, -0.17264284, 0.14315751, 0.04552... -32.769390  -9.923114   
2  [[0.033576064, 0.11381981, 0.03323982, 0.10893...   1.073096  15.113221   
3  [[0.15828276, -0.19332649, 0.03358131, -0.0077...  25.016422 -44.813076   
4  [[0.13633102, 0.021079788, -0.220977, -0.17637...  19.098520  55.694305   

           Z  
0  66.206818  
1 -37.638607  
2 -33.401627  
3  13.185284  
4 -39.759186

#### Representación de los resultados

Para poder observar mejor los resultados se han representado tanto en 2D como en 3D. En ambas representaciones se muestra una gran concentración de puntos en un espacio determinado, no existiendo una clara separación de los datos. Cada punto corresponde a una canción y los colores son los artistas de las canciones. Esto apoya las conclusiones obtenidas tras realizar la exploración del modelo, en el que se decía que el modelo no ofrece buenos resultados seguramente por la calidad de los datos de entrada.

In [364]:
import plotly.graph_objects as go
import numpy as np

fig = go.Figure(data=go.Scatter(
    y = two_dimensional_songs['Y'],
    x = two_dimensional_songs['X'],
    mode='markers',
    marker=dict(
        size=16,
        color=np.random.randn(500), #set color equal to a variable
        colorscale='Viridis', # one of plotly colorscales
        showscale=True
    )
))

fig.show()

In [358]:
import plotly.express as px
# df = px.data.iris()
fig = px.scatter_3d(three_dimensional_songs, x='X', y='Y', z='Z', color='artista')
fig.show()

<img src="image.jpeg">

In [353]:
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

init_notebook_mode(connected=True)

import plotly.graph_objs as go

trace1 = go.Scatter(
    y = two_dimensional_songs['Y'],
    x = two_dimensional_songs['X'],
    text = two_dimensional_songs['letra'],
    mode='markers',
    marker=dict(
        size= [5],#'7',
        color = np.random.randn(5717), #set color equal to a variable
        colorscale='Viridis',
        showscale=True
    )
)
data = [trace1]

iplot(data)

In [354]:
import plotly.graph_objects as go
import numpy as np

fig = go.Figure(data=go.Scatter(
    y = two_dimensional_songs['Y'],
    x = two_dimensional_songs['X'],
    text = two_dimensional_songs['artista']+ "_"+two_dimensional_songs['cancion'] ,
    #text = two_dimensional_songs['letra'] ,
    mode='markers',
    marker=dict(
        size= [10],#'7',
        color = np.random.randn(5717), #set color equal to a variable
        colorscale='Viridis',
        showscale=True
    )
))

fig.show()